In [185]:
import json
skip = [
    'Lime juice',
    'Syrup',
    'Lemon juice',
    'Orange juice',
    'Cream',
    'Soda water',
    'Cola',
    'Hot coffee',
    'Egg yolk',
    'Coconut milk',
    'Ginger beer',
    'Pineapple juice',
    'Grapefruit juice',
    'Cranberry juice',
    'Tomato juice',
    'Olive juice',
    'Ginger Ale',
]
recipesj = json.load(open('recipes-fix.json'))
ingredients = set()
for recipe in recipesj:
    for ingredient in recipe['ingredients']:
        if 'special' in ingredient:
            continue
        if ingredient['ingredient'] in skip:
            continue
        ingredients.add(ingredient['ingredient'])
ingredientsl = list(ingredients)
ingredientsm = dict(zip(ingredientsl, range(len(ingredientsl))))
recipes = []
for recipe in recipesj:
    x = set()
    for ingredient in recipe['ingredients']:
        if 'special' in ingredient:
            continue
        if ingredient['ingredient'] in skip:
            continue
        y = ingredientsm[ingredient['ingredient']]
        x.add(y)
    recipes.append(x)
n_ingredients = len(ingredientsl)
print(ingredientsl)

['Dark rum', 'Dry white wine', 'Créme de Menthe', 'Peach bitters', 'Maraschino', 'Galliano', 'Raspberry syrup', 'Campari', 'Tequila', 'Créme de Cassis', 'DOM Bénédictine', 'Lillet Blonde', 'Sweet vermouth', 'Kirsch', 'Cream liqueur', 'Grenadine', 'Cherry liqueur', 'Calvados', 'Bourbon', 'Aperol', 'Créme de Cacao', 'Triple Sec', 'Absinthe', 'DiSaronno', 'Peach schnapps', 'Rye', 'Coffee liqueur', 'Drambuie', 'Strawberry syrup', 'Irish whiskey', "Peychaud's bitters", 'Raspberry liqueur', 'Scotch', 'Dry vermouth', 'Peach puree', 'Apricot brandy', 'White rum', 'Pisco', 'Orange flower water', 'Prosecco', 'Orange bitters', 'Cognac', 'Angostura bitters', 'Gin', 'Vodka', 'Orgeat', 'Cachaca', 'Blackberry liqueur', 'Champagne', 'Red Port']


In [186]:
makeStepR = lambda step, r: 'r' + str(step) + '_' + str(r)
makeStepY = lambda step, y: 'y' + str(step) + '_' + str(y)

f = open('lp.2', 'w')
f.write('Minimize\n')
for step in range(n_ingredients):
    for r, recipe in enumerate(recipes):
        f.write(' - ' + makeStepR(step, r))
f.write('\nSubject To\n')
for step in range(n_ingredients):
    f.write(' + '.join(makeStepY(step, y) for y in range(n_ingredients)) + ' = ' + str(step + 1) + '\n')
for y in range(n_ingredients):
    for step in range(n_ingredients - 1):
        f.write(makeStepY(step+1, y) + ' - ' + makeStepY(step, y) + ' >= 0\n')
for r, recipe in enumerate(recipes):
    for step in range(n_ingredients):
        tot = ' - '.join(makeStepY(step, y) for y in recipe)
        f.write(makeStepR(step, r) + ' - ' + tot + ' >= -' + str(len(recipe) - 1) + '\n')
        for y in recipe:
            f.write(makeStepR(step, r) + ' - ' + makeStepY(step, y) + ' <= 0\n')
f.write('Binary\n')
f.write(' '.join(makeStepY(step, y) 
                 for step in range(n_ingredients) for y in range(n_ingredients)))
f.write(' ')
f.write(' '.join(makeStepR(step, r) 
                 for step in range(n_ingredients) for r in range(len(recipes))))
f.write('\nEnd\n')
f.close()

In [164]:
linesf = open('sol.2')
lines = linesf.read().splitlines()
linesf.close()
sol = []
seen = set()
batch = None
batches = []
oldstep = None
for line in lines:
    if 'y' in line:
        y = line.split()[1].split('_')[-1]
        if int(y) in sol:
            continue
        sol.append(int(y))
    if 'r' in line:
        step, r = line.split()[1][1:].split('_')
        step = int(step)
        r = int(r)
        if step != oldstep:
            if batch is not None:
                batches.append((oldstep, batch))
            batch = []
            oldstep = step
        if r not in seen:
            batch.append(r)
        seen.add(r)
batches.append((oldstep, batch))
len(batches), len(sol)

(50, 50)

In [166]:
def pad(s, n):
    return s + (n - len(s))*' '
for i, (y, (step, batch)) in enumerate(zip(sol, batches)):
    drinks = [recipesj[r]['name'] for r in batch]
    print(pad(str(i+1) + '. ' + ingredientsl[y], 23) + ' | ' + ', '.join(drinks))

1. Vodka                | Sea Breeze, Screwdriver, Bloody Mary, Moscow Mule
2. White rum            | Mojito, Cuba Libre, Pina Colada, Daiquiri
3. Triple Sec           | Lemon Drop Martini, Cosmopolitan, Kamikaze
4. Tequila              | Margarita, Tommy's Margarita, Vampiro
5. Gin                  | Long Island Iced Tea, Gin Fizz, John Collins, White Lady
6. Cognac               | Horse's Neck, Sidecar, Between the Sheets
7. Galliano             | Yellow Bird, Golden Dream, Harvey Wallbanger
8. Cherry liqueur       | Aviation, Hemingway Special
9. Grenadine            | Bacardi, Tequila Sunrise, Mary Pickford
10. Bourbon             | Whiskey Sour, Mint Julep
11. Champagne           | Mimosa, French 75
12. Angostura bitters   | Old Fashioned, Champagne Cocktail
13. DiSaronno           | God Mother, French Connection
14. Dark rum            | Planter's Punch, Dark 'n' Stormy
15. Dry vermouth        | Dirty Martini, Dry Martini
16. Coffee liqueur      | Espresso Martini, Black Russian


In [169]:
from collections import Counter
recipesc = recipes.copy()
greedysol = []

for step in range(n_ingredients):
    c = Counter()
    for recipe in recipesc:
        if len(recipe) == 1:
            c.update([list(recipe)[0]])
    ingrs = c.most_common()
    if len(ingrs) == 0:
        ingr = list(set.union(*recipesc))[0]
    else:
        ingr = ingrs[0][0]
    greedysol.append(ingr)
    for i, recipe in enumerate(recipesc):
        recipesc[i] = recipe - {ingr}
for y in greedysol:
    print(ingredientsl[y])

White rum
Vodka
Triple Sec
Cognac
Gin
Tequila
Galliano
Grenadine
Cherry liqueur
Champagne
Bourbon
Angostura bitters
Dark rum
Coffee liqueur
DiSaronno
Dry vermouth
Lillet Blonde
Pisco
Raspberry syrup
Red Port
Cream liqueur
Créme de Menthe
Créme de Cacao
Blackberry liqueur
Raspberry liqueur
Orgeat
Prosecco
Peach puree
Aperol
Peach schnapps
Absinthe
Peach bitters
Irish whiskey
Peychaud's bitters
DOM Bénédictine
Apricot brandy
Calvados
Orange flower water
Créme de Cassis
Dry White Wine
Scotch
Drambuie
Orange Bitters
Maraschino
Cachaca
Campari
Sweet vermouth
Rye
Kirsch
Strawberry syrup


In [174]:
def score(recipes, sol):
    t = 0
    recipesc = recipes.copy()
    for i, y in enumerate(sol):
        for recipe in recipesc:
            if recipe == {y}:
                t += (len(ingredientsl)-i)
        for i, recipe in enumerate(recipesc):
            recipesc[i] = recipe - {y}
    return t

In [175]:
score(recipes, sol), score(recipes, greedysol)

(2501, 2495)